# Train node2vec

In [1]:
%matplotlib inline

import warnings
warnings.filterwarnings('ignore')
import os
import collections
import pandas as pd
from sklearn.manifold import TSNE
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import seaborn as sns
from node2vec import Node2Vec

In [3]:
# ------------------ number of citations for labeled data -------------- #
Dataset = "pubmed"
citation_edges = []
citation_path = "Data/"+Dataset+"/labeled_subgraph.txt"
# read in paper ID
with open(citation_path, 'r', encoding = 'utf8') as infile:
    for line in infile:
        citation_edges.append((line.strip("\n").split("\t")[0], line.strip("\n").split("\t")[1]))
print(len(citation_edges))
duplicate_counter = collections.Counter(citation_edges)
duplicate_list = [i for i, cnt in duplicate_counter.items() if cnt > 1]
print(duplicate_counter.most_common(5))
print("Total duplicate links: ",len(duplicate_list))
Unique_citation_edges = list(set(citation_edges))
print(len(Unique_citation_edges))

6080487
[(('23754339', '10.1023/a:1005596502855'), 2), (('23754339', '10.1177/0829573507302967'), 2), (('23754339', '10.1023/a:1005592401947'), 2), (('23824667', '10.1016/j.biombioe.2006.02.004'), 2), (('23824667', '10.1109/tia.1997.649985'), 2)]
Total duplicate links:  12579
6067908


In [4]:
print(Unique_citation_edges[0])
for item in Unique_citation_edges:
    print(item[0])
    print(item[1])
    break

('23269734', '21236728')
23269734
21236728


In [5]:
# ---------------- number of labeled paper in source/target pid ---------------- #
fileDir = "Data/pubmed/canopies_labeled/"
listfiles = os.listdir(fileDir)
LabeledRecords_pid = []

for file in listfiles:
    if not file.startswith('.'):
        with open(fileDir+file, 'r', encoding = 'utf8') as f:
            for line in f:
                read_data = line.split("\t")
                if(len(read_data)==13 or len(read_data)==12):
                    LabeledRecords_pid.append(read_data[0])
                else:
                    print(len(read_data))
        f.close()
print("Total record: ", len(LabeledRecords_pid))
labeled_unique_paperIDs = set(LabeledRecords_pid)
print("Total paper: ", len(labeled_unique_paperIDs))

source_list = [item[0] for item in Unique_citation_edges if item[0] in labeled_unique_paperIDs]
labeled_never_occur_in_source = [item for item in Unique_citation_edges if item[0] not in labeled_unique_paperIDs]
target_list = [item[1] for item in Unique_citation_edges if item[1] in labeled_unique_paperIDs]
labeled_never_occur_in_target = [item for item in Unique_citation_edges if item[1] not in labeled_unique_paperIDs]

labeled_never_occur = list(set(labeled_never_occur_in_source) & set(labeled_never_occur_in_target)) 

print(source_list[:10])
print(len(source_list),"papers appear as source node")
print(target_list[:10])
print(len(target_list),"papers appear as target node")
print(len(labeled_never_occur),"labeled papers have never occur")
unique_nodes = set([node for edge in Unique_citation_edges for node in edge])
print(len(unique_nodes), "unique node from graph")


Total record:  140266
Total paper:  135796
['24317402', '23943234', '22632366', '25990816', '19902479', '21675585', '22484702', '24795878', '22933327', '15798198']
3309530 papers appear as source node
['21236728', '11604223', '24587896', '17174575', '16093438', '16896909', '18429609', '12808463', '22088360', '16798971']
2939910 papers appear as target node
0 labeled papers have never occur
3585267 unique node from graph


In [22]:
# --------- construct graph ------------- #
import networkx as nx
print(len(citation_edges))
print(len(Unique_citation_edges))
citation_G=nx.Graph()

repreated_edge = []

for edge in citation_edges:
    if citation_G.has_edge(*edge):
        repreated_edge.append(edge)
    citation_G.add_edge(*edge)
print(repreated_edge[:10])
print(len(repreated_edge))

6080487
6067908
[('18600692', '18600693'), ('18600692', '18600694'), ('18600693', '18600694'), ('12203992', '12203987'), ('7815092', '7815093'), ('1717683', '1920161'), ('24232407', '24232358'), ('2502792', '2502793'), ('7094986', '7041454'), ('24420429', '24420430')]
13907


In [23]:
# ---------- collect graph statistic ----- #
print("Is directed graph: ",nx.is_directed(citation_G))
print(nx.info(citation_G))
node_count = citation_G.number_of_nodes()
edge_count = citation_G.number_of_edges()
# return sum of degree (Sum of indegree and outdegree)
citation_degrees = dict(citation_G.degree())
sum_of_edges = sum(citation_degrees.values())
average_degrees = sum_of_edges/len(citation_G)
print(type(citation_degrees))
print(sum_of_edges)
print(average_degrees)
# find max degree paper
max_degree = max(citation_degrees.values())
max_degree_item = [node for node in citation_degrees if citation_degrees[node]==max_degree]
print(max_degree)
print(max_degree_item)

Is directed graph:  False
Name: 
Type: Graph
Number of nodes: 3585267
Number of edges: 6066580
Average degree:   3.3842
<class 'dict'>
12133160
3.3841719459108623
9909
['10802651']


In [18]:
# nx.draw(citation_G)
# plt.show()

In [ ]:
# Precompute probabilities and generate walks - **ON WINDOWS ONLY WORKS WITH workers=1**
node2vec = Node2Vec(citation_G, dimensions=100, walk_length=60, num_walks=10, workers=1)


Computing transition probabilities:   0%|          | 1415/3585267 [00:14<12:09:35, 81.87it/s]


Computing transition probabilities:   0%|          | 3137/3585267 [00:26<8:08:57, 122.10it/s]


Computing transition probabilities:   0%|          | 4815/3585267 [00:37<13:54:55, 71.47it/s]


Computing transition probabilities:   0%|          | 6773/3585267 [00:48<5:06:37, 194.51it/s]


Computing transition probabilities:   0%|          | 8446/3585267 [00:59<9:47:46, 101.42it/s]


...

Computing transition probabilities:  74%|███████▎  | 2643345/3585267 [1:38:09<28:14, 555.80it/s]


Computing transition probabilities:  74%|███████▍  | 2648784/3585267 [1:38:18<31:21, 497.81it/s]


Computing transition probabilities:  74%|███████▍  | 2653478/3585267 [1:38:29<41:55, 370.46it/s]


Computing transition probabilities:  74%|███████▍  | 2658821/3585267 [1:38:40<33:13, 464.84it/s]


Computing transition probabilities:  74%|███████▍  | 2662476/3585267 [1:38:47<32:08, 478.45it/s]

In [ ]:
%tb

In [ ]:
print(dir(node2vec))

In [ ]:
# Embed nodes
model = node2vec.fit(window=10, min_count=1)

In [ ]:
print(dir(model))

In [ ]:
print(dir(model.wv))

In [ ]:
print(len(model.wv.vocab))
print(dict(list(model.wv.vocab.items())[:10]))

In [ ]:
2011361
{'7935409': <gensim.models.keyedvectors.Vocab object at 0x7f17e51f3f98>, '16793553': <gensim.models.keyedvectors.Vocab object at 0x7f17e4d3ef60>, '7584145': <gensim.models.keyedvectors.Vocab object at 0x7f2e2b728048>, '10.1126/science.291.5507.1155d': <gensim.models.keyedvectors.Vocab object at 0x7f2e2b728a90>, '11891060': <gensim.models.keyedvectors.Vocab object at 0x7f2e2b728320>, '8338689': <gensim.models.keyedvectors.Vocab object at 0x7f2e2b7280f0>, '10570990': <gensim.models.keyedvectors.Vocab object at 0x7f2e2b732ba8>, '9367984': <gensim.models.keyedvectors.Vocab object at 0x7f2e2b732b70>, '17996480': <gensim.models.keyedvectors.Vocab object at 0x7f1a0526ee80>, '10036187': <gensim.models.keyedvectors.Vocab object at 0x7f17e4958a58>}

In [ ]:
print(dir(model.save))

In [33]:
# -----------------   save model ------------------ #
import os
# ----- generate file name ------------ #
newfileDir = "models/"+Dataset+"/node2vec/"
if not os.path.exists(newfileDir):
    os.makedirs(newfileDir)
modelname = model.__str__()+"(node2vec)"
EMBEDDING_FILENAME = newfileDir+modelname
EMBEDDING_MODEL_FILENAME = newfileDir+modelname

# save embedding
model.wv.save_word2vec_format(EMBEDDING_FILENAME)
# Save model for later use
model.save(EMBEDDING_MODEL_FILENAME)

In [16]:
# ------------- save vector trained as txt --------------- #
import os
newfileDir = "vectors/"+Dataset+"/node2vec/"
if not os.path.exists(newfileDir):
    os.makedirs(newfileDir)
modelname = model.__str__()+"(node2vec)"
EMBEDDING_FILENAME = newfileDir+modelname+".txt"

# Save embeddings for later use
model.wv.save_word2vec_format(EMBEDDING_FILENAME)

In [34]:
print("Done")

Done
